In [1]:
import numpy as np
import pandas as pd
import os
import pywikibot
import pickle

In [4]:
# Obtained from Temporal ranking Paper
#data = np.load("NASDAQ_wiki_relation.npy")
ticker_wikicode_map_df = pd.read_csv("NASDAQ_ticker_to_wiki.csv")

ticker_wikicode_map_nyse_df = pd.read_csv("NYSE_ticker_to_wiki.csv")


# Tickers that are selected for training the model
INDEX = "nasdaq100"

directory = "../../../data/" + INDEX + "/"

ticker_list = {}
for filename in os.listdir(directory):
    f = os.path.join(directory, filename)
    if os.path.isfile(f):
        ticker, name = filename.split("-")

        df = pd.read_csv(f)

        if df.shape[0] <= 2600: 
            continue 
        
        ticker_list[ticker] = [name]

INDEX = "sp500"

directory = "../../../data/" + INDEX + "/"

for filename in os.listdir(directory):
    f = os.path.join(directory, filename)
    if os.path.isfile(f):
        ticker, name = filename.split("-")

        df = pd.read_csv(f)

        if df.shape[0] <= 2600: 
            continue 
        
        ticker_list[ticker] = [name]

print(len(ticker_list.keys()))
print(ticker_list.keys())

# Getting the WikiBase Id for the companies
# Some of the wanted tickers are not available.
wikicode_map = {}
for index, row in ticker_wikicode_map_df.iterrows():
    if row[0] in ticker_list:
        if row[1] == 'unknown':
            continue
        wikicode_map[row[0]] = row[1]

for index, row in ticker_wikicode_map_nyse_df.iterrows():
    if row[0] in ticker_list:
        if row[1] == 'unknown':
            continue
        wikicode_map[row[0]] = row[1]

print(len(wikicode_map.values()), len(ticker_list.values()))

# Obtained from Wikibase Query builder, using filter
# key 'part of' and value 's&p500
sp500_id = pd.read_csv("query.csv")

ticker_maps_mine = {}
for i in range(528):
    id = sp500_id.loc[i]['item'].split("/")[-1]
    print(sp500_id.loc[i])
    site = pywikibot.Site("wikidata", "wikidata")
    repo = site.data_repository()
    item = pywikibot.ItemPage(repo, id)
    item_dict = item.get()
    try:
        d = item_dict['claims']['P414']
        ticker = d[0].qualifiers['P249'][0].toJSON()['datavalue']['value']

        ticker_maps_mine[ticker] = id
    except:
        print("Not available")

# Even then, IDs for some tickers were not available, so I manually searched wikibase with company names
# and obtained the ID
my_map = {
    'MNST': 'Q1945295',
    'WBA': 'Q18712620',
    'EBAY': 'Q58024',
    'ENPH': 'Q17012234',
    'MTCH': 'Q23133268',
    'CHTR': 'Q2961234',
    'TMUS': 'Q3511885',
    'SIRI': 'Q3277465',
    'BKNG': 'Q18674747',
    'AMD': 'Q128896',
    'AVGO': 'Q4827416',
    'KDP': 'Q3116111',
    'SPLK': 'Q1835753',
    'CTRA': 'Q4035714',
    'PENN': 'Q7163201',
    'NEM': 'Q1785405',
    'GNRC': 'Q5531627',
    'TFC': 'Q795486',
    'PTC': 'Q1760641',
    'BKR': 'Q804353',
    'UAA': 'Q2031485',
    'SPGI': 'Q868587'    
}

ticker_id_map = {}
for ticker, val in ticker_list.items():
    if ticker in ticker_maps_mine:
        ticker_id_map[ticker] = ticker_maps_mine[ticker]
    elif ticker in my_map:
        ticker_id_map[ticker] = my_map[ticker]
    elif ticker in wikicode_map:
        ticker_id_map[ticker] = wikicode_map[ticker]
print(len(ticker_id_map.keys()))

with open('ticker_wiki_map.pkl', 'wb') as f:
    pickle.dump(ticker_id_map, f)

461
dict_keys(['SBUX', 'VRSK', 'ADBE', 'NVDA', 'AMGN', 'ISRG', 'KLAC', 'AAPL', 'REGN', 'BIDU', 'QCOM', 'XEL', 'MNST', 'CTSH', 'EA', 'WBA', 'ADSK', 'EBAY', 'ILMN', 'NTES', 'SWKS', 'SPLK', 'ADP', 'MU', 'AMZN', 'MCHP', 'NXPI', 'FTNT', 'SGEN', 'TXN', 'ENPH', 'DXCM', 'AZN', 'VRSN', 'MTCH', 'CHTR', 'AMAT', 'FISV', 'TMUS', 'MSFT', 'CTAS', 'IDXX', 'TSLA', 'MAR', 'AEP', 'NFLX', 'CDNS', 'ALGN', 'MELI', 'GILD', 'SIRI', 'EXC', 'CSCO', 'LULU', 'GOOGL', 'MRVL', 'ASML', 'BIIB', 'GOOG', 'BKNG', 'FAST', 'ORLY', 'ROST', 'VRTX', 'PCAR', 'CMCSA', 'PEP', 'ATVI', 'AMD', 'ANSS', 'AVGO', 'INTU', 'SNPS', 'COST', 'DLTR', 'PANW', 'HON', 'INTC', 'PAYX', 'CSX', 'LRCX', 'ADI', 'MDLZ', 'KDP', 'CPRT', 'ODFL', 'META', 'APH', 'PG', 'OMC', 'AMCR', 'KMX', 'STE', 'SPG', 'GE', 'TMO', 'PNR', 'EIX', 'SCHW', 'EQR', 'GIS', 'TRMB', 'FCX', 'UPS', 'FDX', 'SYY', 'COF', 'LEN', 'WELL', 'HSIC', 'BDX', 'BEN', 'LLY', 'VFC', 'WFC', 'WHR', 'UNP', 'FMC', 'GPC', 'ABT', 'IVZ', 'WAT', 'WEC', 'ROK', 'BRO', 'LNC', 'AME', 'TDY', 'DAL', 'CTRA', 

In [4]:
with open('ticker_wiki_map.pkl', 'rb') as f:
    ticker_wiki_map = pickle.load(f)

In [5]:
inverse_ticker_wiki_map = {ticker_wiki_map[k] : k for k in ticker_wiki_map}

In [2]:
# Relations to consider
relation_map = {
    'P127': 'Owned By - FO',
    'P155': 'Follows - FO',
    'P156': 'Followed By - FO',
    'P355': 'Subsidiary - FO',
    'P749': 'Parent Organisation - FO',
    'P31': 'Instance of',
    'P366': 'Use',
    'P452': 'Industry', 
    'P1056': 'Product or Material Produced',
    'P112': 'Founded By',
    'P169': 'CEO',
    'P113': 'Airline Hub',
    'P114': 'Airline Alliance',
    'P121': "Item Operated",
    'P1830': 'Owner of - FO',
    'P3320': 'Board Member',
    'P166': 'Award received',
    'P199': 'Business Division',
    'P361': 'Part of',
    'P400': 'Platform',
    'P2770': 'Source of Income',
    'P463': 'Member of',
    'P306': 'Operating System',
    'P1344': 'Participant of'
}

In [3]:
wiki_relations = {}

with open('wiki_relations_value.pkl', 'rb') as f:
    wiki_relations = pickle.load(f)

In [6]:
for relation, rel_label in relation_map.items():
    for ticker, wiki_id in ticker_wiki_map.items():
        if (ticker, relation) in wiki_relations:
            continue

        site = pywikibot.Site("wikidata", "wikidata")
        repo = site.data_repository()
        item_dict = pywikibot.ItemPage(repo, wiki_id).get()
        claims = item_dict['claims']

        try:
            value = claims[relation]
            for snaks in value:
                snak = snaks.toJSON()
                snak_value = snak['mainsnak']['datavalue']['value']['numeric-id']
                wiki_relations[(ticker, relation)] = wiki_relations.get((ticker, relation), []) + [snak_value]
            print(ticker, relation, rel_label, wiki_relations[(ticker, relation)])
        except:
            wiki_relations[(ticker, relation)] = None

TTWO P463 Member of [55524865]
RMD P463 Member of [7389502]
BA P463 Member of [37033, 1361045]
PNC P463 Member of [15731702]
BR P463 Member of [858851]
WDC P463 Member of [60535625, 858851]
KR P463 Member of [79100838]
DIS P463 Member of [37033]
JNPR P463 Member of [858851, 67904121, 1685617]
GS P463 Member of [858851, 15731702, 1663567]
MMM P463 Member of [1203027]
JCI P463 Member of [67904121]
CRM P463 Member of [858851, 37033, 67904121, 2025721, 852297]
STT P463 Member of [858851]
ITW P463 Member of [7389502]
T P463 Member of [37033, 455048]
NOW P463 Member of [852297]
STX P463 Member of [858851, 1361045]
MRK P463 Member of [2513915, 422557, 463681, 1008895, 1454899, 2513764, 16974387, 1005586, 1005597, 111512539, 30094500]
CHTR P1344 Participant of [62562301]
PEP P1344 Participant of [1107563]
META P1344 Participant of [55696286]
BAX P1344 Participant of [928528]
LUMN P1344 Participant of [62562301]
KO P1344 Participant of [1107563]


In [7]:
with open('wiki_relations_value.pkl', 'wb') as f:
    pickle.dump(wiki_relations, f)

In [8]:
with open('wiki_relations_value.pkl', 'rb') as f:
    wiki_relations = pickle.load(f)

In [9]:
relation_knowledge_graph = []

In [10]:
# First-order relation
for key, value in wiki_relations.items():
    if value is None:
        continue
    for ids in value:
        if 'Q'+str(ids) in inverse_ticker_wiki_map:
            print(key, inverse_ticker_wiki_map['Q'+str(ids)])
            relation_knowledge_graph.append((key[0], key[1], inverse_ticker_wiki_map['Q'+str(ids)]))

('NVDA', 'P127') BLK
('AAPL', 'P127') BLK
('MNST', 'P127') KO
('EBAY', 'P127') BLK
('AMZN', 'P127') BLK
('AZN', 'P127') BLK
('MSFT', 'P127') BLK
('MSFT', 'P127') STT
('MSFT', 'P127') BLK
('TSLA', 'P127') TROW
('TSLA', 'P127') TROW
('NFLX', 'P127') BLK
('NFLX', 'P127') MS
('NFLX', 'P127') BLK
('GILD', 'P127') BLK
('GOOGL', 'P127') BLK
('GOOGL', 'P127') BLK
('GOOG', 'P127') BLK
('GOOG', 'P127') BLK
('PEP', 'P127') BLK
('META', 'P127') BLK
('GE', 'P127') TROW
('GE', 'P127') BLK
('GE', 'P127') NTRS
('WFC', 'P127') BLK
('JPM', 'P127') BLK
('C', 'P127') BLK
('WU', 'P127') BLK
('WU', 'P127') STT
('MS', 'P127') STT
('MS', 'P127') BLK
('MS', 'P127') TROW
('CAT', 'P127') STT
('CAT', 'P127') BLK
('JNJ', 'P127') BLK
('JNJ', 'P127') STT
('MCD', 'P127') BLK
('MCD', 'P127') STT
('IBM', 'P127') STT
('VZ', 'P127') BLK
('XOM', 'P127') STT
('XOM', 'P127') BLK
('XOM', 'P127') BLK
('BAC', 'P127') BLK
('DRI', 'P127') GIS
('GLW', 'P127') BLK
('COP', 'P127') BLK
('PFE', 'P127') BLK
('PFE', 'P127') STT
('DHR',

In [11]:
second_order_relation_types = ['P452_P452', 'P127_P127', 'P355_P355', 'P355_P199', 
                  'P112_P112', 'P112_P127', 'P112_P169', 'P169_P112', 'P169_P127', 'P169_P169', 'P127_P112',
                  'P127_P169', 'P31_P366', 'P127_P3320', 'P463_P463', 'P1056_P306', 'P1056_P1056',
                  'P1056_P452', 'P31_P452', 'P199_P355', 'P452_P2770', 'P1344_P1344',
                  'P169_P3320', 'P452_P31', 'P452_P1056', 'P306_P1056', 'P121_P121', 'P31_P1056', 'P166_P166',
                  '2770_P452', 'P366_P31', 'P1056_P31', 'P400_P1056', 'P3320_P127', 'P3320_P169', 'P1056_P400',
                  'P114_P114', 'P121_P1056', 'P113_P113', 'P127_P749', 'P127_P355', 'P749_P127', 'P1830_P127', 
                  'P1830_P749', 'P355_P127', 'P155_P355', 'P155_P155', 'P355_P155', 'P127_P1830', 'P749_P1830',
                  'P1056_P121']
first_order_relation_types = ['P355', 'P155', 'P127', 'P156', 'P749', 'P1830']
print(len(second_order_relation_types))

51


In [12]:
for relation in second_order_relation_types:
    r1, r2 = relation.split('_')
    for ticker, wiki_id in ticker_wiki_map.items():
        value1 = wiki_relations[(ticker, r1)]
        if value1 is None:
            continue
        for ticker2, wiki_id2 in ticker_wiki_map.items():
            value2 = wiki_relations[(ticker, r2)]
            if value2 is None:
                continue
            if set(value1).intersection(set(value2)) and ticker != ticker2:
                print(ticker, relation, ticker2)
                relation_knowledge_graph.append((ticker, relation, ticker2))

SBUX P452_P452 VRSK
SBUX P452_P452 ADBE
SBUX P452_P452 NVDA
SBUX P452_P452 AMGN
SBUX P452_P452 ISRG
SBUX P452_P452 KLAC
SBUX P452_P452 AAPL
SBUX P452_P452 REGN
SBUX P452_P452 BIDU
SBUX P452_P452 QCOM
SBUX P452_P452 XEL
SBUX P452_P452 MNST
SBUX P452_P452 CTSH
SBUX P452_P452 EA
SBUX P452_P452 WBA
SBUX P452_P452 ADSK
SBUX P452_P452 EBAY
SBUX P452_P452 ILMN
SBUX P452_P452 NTES
SBUX P452_P452 SWKS
SBUX P452_P452 SPLK
SBUX P452_P452 ADP
SBUX P452_P452 MU
SBUX P452_P452 AMZN
SBUX P452_P452 MCHP
SBUX P452_P452 NXPI
SBUX P452_P452 FTNT
SBUX P452_P452 SGEN
SBUX P452_P452 TXN
SBUX P452_P452 ENPH
SBUX P452_P452 DXCM
SBUX P452_P452 AZN
SBUX P452_P452 VRSN
SBUX P452_P452 MTCH
SBUX P452_P452 CHTR
SBUX P452_P452 AMAT
SBUX P452_P452 FISV
SBUX P452_P452 TMUS
SBUX P452_P452 MSFT
SBUX P452_P452 CTAS
SBUX P452_P452 IDXX
SBUX P452_P452 TSLA
SBUX P452_P452 MAR
SBUX P452_P452 AEP
SBUX P452_P452 NFLX
SBUX P452_P452 CDNS
SBUX P452_P452 ALGN
SBUX P452_P452 MELI
SBUX P452_P452 GILD
SBUX P452_P452 SIRI
SBUX P452_P